In [75]:
from census import Census
from config import (api_key)
import pandas as pd
import geopandas as gpd
import us
import numpy as np
import matplotlib.pyplot as plt
import requests
import scipy.stats as st
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
import shapely
import shapefile
import plotly.express as px


# Output File (CSV)
output_data_file = "output_data/output_race.csv"

# Census API Key
c = Census(api_key, year=2016)

# US states abbrv mapping
states = us.states.mapping('abbr', 'name')
states = {state: abbrev for abbrev, state in states.items()}

In [3]:
#load police killing data
file_path = "../police_killings.csv"

police_df = pd.read_csv(file_path)
police_df = police_df.rename(columns={ "Victim's race": "race",
                                     "State": "state"})

police_df = police_df.replace({'Unknown race': 'Unknown',
                              "Unknown Race" : "Unknown"})

In [4]:

# Run Census Search to retrieve data on all zip codes (2013 ACS5 Census)
# See: https://github.com/CommerceDataService/census-wrapper for library documentation
# See: https://gist.github.com/afhaque/60558290d6efd892351c4b64e5c01e9b for labels

census_data = c.acs5.get(("NAME", "B01003_001E","B02001_002E", 
                          "B02001_003E", "B02001_004E", 
                          "B02001_005E", "B02001_006E", 
                          "B02001_008E", "B03001_003E"
                         ), {'for': 'zip code tabulation area:*'})

# Convert to DataFrame
census_pd = pd.DataFrame(census_data)

#rename columns 
census_pd = census_pd.rename(columns={ "B01003_001E": "population",
                                      "B02001_002E": "white",
                                      "B02001_003E": "black",
                                      "B02001_004E" : "native",
                                      "B02001_005E" : "asian",
                                      "B02001_006E" : "native_h",
                                      "B02001_008E" : "mixed",
                                      "B03001_003E" : "hispanic"})


# Visualize
print(len(census_pd))
census_pd.head()

33120


NAME  population    white   black  native   asian  native_h  mixed  \
0  ZCTA5 37064     54462.0  48859.0  3662.0    23.0   687.0       0.0  887.0   
1  ZCTA5 37066     46969.0  39015.0  5564.0   205.0   260.0     105.0  833.0   
2  ZCTA5 37067     26841.0  22140.0   989.0    22.0  2854.0       0.0  623.0   
3  ZCTA5 37069     19522.0  18335.0   380.0    38.0   388.0      16.0  358.0   
4  ZCTA5 37072     31914.0  25668.0  4754.0   348.0   227.0       0.0  490.0   

   hispanic zip code tabulation area  
0    3686.0                    37064  
1    3602.0                    37066  
2    1050.0                    37067  
3     372.0                    37069  
4    1446.0                    37072

In [5]:
census_data_fips = c.acs5.get(("NAME", "B01003_001E","B02001_002E", 
                          "B02001_003E", "B02001_004E", 
                          "B02001_005E", "B02001_006E", 
                          "B02001_008E", "B03001_003E"), {'for': 'state:*', 'for':'county:*'})

# Convert to DataFrame
census_fips_pd = pd.DataFrame(census_data_fips)

# Column Reordering
census_fips_pd = census_fips_pd.rename(columns={ "B01003_001E": "population",
                                      "B02001_002E": "white",
                                      "B02001_003E": "black",
                                      "B02001_004E" : "native",
                                      "B02001_005E" : "asian",
                                      "B02001_006E" : "native_h",
                                      "B02001_008E" : "mixed",
                                      "B03001_003E" : "hispanic",
                                      "NAME": "Name",
                                      "state": "State ID",
                                      "county": "County ID"})

# Final DataFrame
#census_fips_pd = census_fips_pd[["Name", "State ID", "County ID", "Population", "Poverty Rate"]]

# Check if any rows with NAN values
census_fips_pd[census_fips_pd.isna().any(axis=1)]

# Drop any rows with NAN
#census_fips_pd = census_fips_pd.dropna(how='any')
census_fips_pd

Name  population     white    black  \
0              Carroll County, Arkansas     27690.0   25856.0    318.0   
1               Chicot County, Arkansas     11189.0    4778.0   6070.0   
2                Clark County, Arkansas     22684.0   16387.0   5348.0   
3                 Clay County, Arkansas     15202.0   14632.0     76.0   
4             Cleburne County, Arkansas     25587.0   24850.0    143.0   
...                                 ...         ...       ...      ...   
3215      Manatí Municipio, Puerto Rico     41468.0   35530.0   1737.0   
3216  Juana Díaz Municipio, Puerto Rico     48658.0   25245.0   5234.0   
3217  Río Grande Municipio, Puerto Rico     52479.0   27604.0   6941.0   
3218     Bayamón Municipio, Puerto Rico    192974.0  120384.0  14050.0   
3219   Canóvanas Municipio, Puerto Rico     47174.0   23000.0   6165.0   

      native  asian  native_h    mixed  hispanic State ID County ID  
0      172.0  245.0     143.0    655.0    4021.0       05       015  
1       47.0   46.0       0.0     72.0     578.0       05       017  
2       39.0  174.0       0.0    400.0    1013.0       05       019  
3       62.0   26.0       0.0    164.0     275.0       05       021  
4      103.0  147.0       0.0    279.0     615.0       05       023  
...      ...    ...       ...      ...       ...      ...       ...  
3215    38.0   17.0       0.0    326.0   40919.0       72       091  
3216     8.0   52.0       0.0  13887.0   48522.0       72       075  
3217    76.0  180.0       0.0   1476.0   52199.0       72       119  
3218  1216.0  429.0      16.0  42590.0  191151.0       72       021  
3219    19.0  173.0       0.0    258.0   47066.0       72       029  

[3220 rows x 11 columns]

In [6]:
# Check if any rows with NAN values
census_pd[census_pd.isna().any(axis=1)]

# Drop any rows with NAN
census_pd = census_pd.dropna(how='any')
census_pd

NAME  population    white   black  native   asian  native_h  \
0      ZCTA5 37064     54462.0  48859.0  3662.0    23.0   687.0       0.0   
1      ZCTA5 37066     46969.0  39015.0  5564.0   205.0   260.0     105.0   
2      ZCTA5 37067     26841.0  22140.0   989.0    22.0  2854.0       0.0   
3      ZCTA5 37069     19522.0  18335.0   380.0    38.0   388.0      16.0   
4      ZCTA5 37072     31914.0  25668.0  4754.0   348.0   227.0       0.0   
...            ...         ...      ...     ...     ...     ...       ...   
33115  ZCTA5 97048      6622.0   6165.0    33.0   152.0    41.0       7.0   
33116  ZCTA5 97049      1764.0   1704.0     0.0     8.0    38.0       0.0   
33117  ZCTA5 97050       229.0    200.0     0.0    29.0     0.0       0.0   
33118  ZCTA5 97051     15783.0  14077.0    48.0   287.0   243.0      93.0   
33119  ZCTA5 97053      3045.0   2901.0    44.0     0.0    12.0       0.0   

       mixed  hispanic zip code tabulation area  
0      887.0    3686.0                    37064  
1      833.0    3602.0                    37066  
2      623.0    1050.0                    37067  
3      358.0     372.0                    37069  
4      490.0    1446.0                    37072  
...      ...       ...                      ...  
33115  224.0     165.0                    97048  
33116   14.0      22.0                    97049  
33117    0.0      35.0                    97050  
33118  627.0    1264.0                    97051  
33119   68.0     110.0                    97053  

[33120 rows x 10 columns]

In [7]:
# Data Cleanup
#code done by Matt Enright and repurposed by McRaven
def get_county(address):
    county = address.split("County")[0].strip(" ")
    county = strip_borough(county)
    county = strip_census_area(county)
    county = strip_municipality(county)
    county = strip_parish(county)
    county = strip_state(county)
    return county

def strip_borough(address):
    return address.split("Borough")[0].strip(" ")

def strip_census_area(address):
    return address.split("Census")[0].strip(" ")

def strip_municipality(address):
    return address.split("Municipality")[0].strip(" ")

def strip_parish(address):
    return address.split("Parish")[0].strip(" ")

def strip_state(address):
    return address.split(",")[0].strip(" ")

def get_state(address):
    state = address.split(",")[1]
    # Special case for District of Columbia
    state = state[1:]
    return state

census_fips_pd['County'] = census_fips_pd['Name'].apply(lambda x: f"{get_county(x)}")
census_fips_pd['State Name'] = census_fips_pd['Name'].apply(lambda x: f"{get_state(x)}")

#Drop PR
indicesPR = census_fips_pd.index[census_fips_pd['State ID'] == '72' ].tolist()
census_fips_pd.drop(indicesPR, inplace=True)

# Get state abbreviations
census_fips_pd['State'] = census_fips_pd['State Name'].map(states)

census_clean_pd = census_fips_pd.drop(['Name', 'State Name'], inplace=False, axis = 1)

#census_clean_pd = census_clean_pd[["State", "State ID", "County", "County ID", "Population", "Poverty Rate"]]

# Export into a csv
#census_clean_pd.to_csv(output_data_file, index=False)

census_clean_pd['FIPS'] = census_clean_pd['State ID'] + census_clean_pd['County ID']

census_clean_pd

population    white   black  native  asian  native_h   mixed  hispanic  \
0        27690.0  25856.0   318.0   172.0  245.0     143.0   655.0    4021.0   
1        11189.0   4778.0  6070.0    47.0   46.0       0.0    72.0     578.0   
2        22684.0  16387.0  5348.0    39.0  174.0       0.0   400.0    1013.0   
3        15202.0  14632.0    76.0    62.0   26.0       0.0   164.0     275.0   
4        25587.0  24850.0   143.0   103.0  147.0       0.0   279.0     615.0   
...          ...      ...     ...     ...    ...       ...     ...       ...   
3137     44812.0  41314.0   405.0   398.0  276.0     137.0  1532.0    7107.0   
3138     22623.0  20964.0   168.0    95.0  410.0       0.0   226.0    3433.0   
3139     20893.0  19705.0    39.0   204.0   31.0       0.0   634.0    1872.0   
3140      8351.0   7575.0    66.0    47.0   15.0       0.0   327.0    1166.0   
3141      7175.0   6686.0    18.0     9.0  361.0       0.0   101.0      72.0   

     State ID County ID      County State   FIPS  
0          05       015     Carroll    AR  05015  
1          05       017      Chicot    AR  05017  
2          05       019       Clark    AR  05019  
3          05       021        Clay    AR  05021  
4          05       023    Cleburne    AR  05023  
...       ...       ...         ...   ...    ...  
3137       56       037  Sweetwater    WY  56037  
3138       56       039       Teton    WY  56039  
3139       56       041       Uinta    WY  56041  
3140       56       043    Washakie    WY  56043  
3141       56       045      Weston    WY  56045  

[3142 rows x 13 columns]

In [8]:
file_path = "zip://tl_2019_01_tract.zip!tl_2019_01_tract.shp"
shp_data = gpd.read_file(file_path)
shp_data.head()

STATEFP COUNTYFP TRACTCE        GEOID    NAME             NAMELSAD  MTFCC  \
0      01      055  010700  01055010700     107     Census Tract 107  G5020   
1      01      055  001300  01055001300      13      Census Tract 13  G5020   
2      01      055  000900  01055000900       9       Census Tract 9  G5020   
3      01      055  001700  01055001700      17      Census Tract 17  G5020   
4      01      055  010501  01055010501  105.01  Census Tract 105.01  G5020   

  FUNCSTAT     ALAND   AWATER     INTPTLAT      INTPTLON  \
0        S  87404337  2927199  +34.0726595  -085.8991944   
1        S   5083957   836213  +34.0078782  -085.9865947   
2        S  11932347   740907  +34.0003469  -086.0427603   
3        S   9118882        0  +33.9825311  -085.9518384   
4        S  50209675  7198559  +33.8992688  -086.0295803   

                                            geometry  
0  POLYGON ((-85.98699 34.04413, -85.98606 34.045...  
1  POLYGON ((-86.00068 34.00537, -86.00023 34.006...  
2  POLYGON ((-86.07079 34.00011, -86.07076 34.000...  
3  POLYGON ((-85.96885 33.98825, -85.96884 33.988...  
4  POLYGON ((-86.07352 33.90549, -86.07337 33.906...

In [9]:
shp_data['FIPS'] = shp_data['STATEFP'] + shp_data['COUNTYFP']
shp_data_clean = shp_data.drop(shp_data.iloc[:, 2:13], inplace = False, axis = 1)
shp_data_clean

STATEFP COUNTYFP   FIPS
0         01      055  01055
1         01      055  01055
2         01      055  01055
3         01      055  01055
4         01      055  01055
...      ...      ...    ...
1176      01      077  01077
1177      01      077  01077
1178      01      077  01077
1179      01      119  01119
1180      01      097  01097

[1181 rows x 3 columns]

In [10]:
killings_df = police_df.drop(police_df.iloc[:, 11:], inplace = False, axis = 1) 
killings_df.drop(['URL of image of victim'], inplace=True, axis = 1)

killings_df.dropna(how='any')
killings_df

Victim's name Victim's age Victim's gender      race  \
0              Eric M. Tellez           28            Male     White   
1     Name withheld by police          NaN            Male   Unknown   
2                Terry Hudson           57            Male     Black   
3              Malik Williams           23            Male     Black   
4           Frederick Perkins           37            Male     Black   
...                       ...          ...             ...       ...   
7658              Mark Chavez           49            Male  Hispanic   
7659               Tyree Bell           31            Male     Black   
7660      Christopher Tavares           21            Male  Hispanic   
7661        Andrew L. Closson           21            Male     White   
7662            Andrew Layton           26            Male     White   

     Date of Incident (month/day/year)             Street Address of Incident  \
0                             31-12-19                             Broad St.    
1                             31-12-19                         7239-7411 I-40   
2                             31-12-19                         3600 N 24th St   
3                             31-12-19                30800 14th Avenue South   
4                             31-12-19                    17057 N Outer 40 Rd   
...                                ...                                    ...   
7658                          01-01-13                    912 Loma Linda Ave.   
7659                          01-01-13                       3727 N. 42nd St.   
7660                          01-01-13  Highway 50 and North Elizabeth Street   
7661                          01-01-13                        U.S. Highway 53   
7662                          01-01-13                 410 S Riverfront Drive   

              City state  Zipcode      County  
0            Globe    AZ  85501.0        Gila  
1          Memphis    AR  38103.0  Crittenden  
2            Omaha    NE  68110.0     Douglas  
3      Federal Way    WA  98003.0        King  
4     Chesterfield    MO  63005.0   St. Louis  
...            ...   ...      ...         ...  
7658    Farmington    NM  87401.0    San Juan  
7659         Omaha    NE  68111.0     Douglas  
7660        Pueblo    CO  81008.0      Pueblo  
7661        Gordon    WI  54838.0     Douglas  
7662       Mankato    MN  56001.0  Blue Earth  

[7663 rows x 10 columns]

In [11]:
police_df = killings_df
police_df["County_State"] = police_df.County + ", " + police_df.state
police_df

Victim's name Victim's age Victim's gender      race  \
0              Eric M. Tellez           28            Male     White   
1     Name withheld by police          NaN            Male   Unknown   
2                Terry Hudson           57            Male     Black   
3              Malik Williams           23            Male     Black   
4           Frederick Perkins           37            Male     Black   
...                       ...          ...             ...       ...   
7658              Mark Chavez           49            Male  Hispanic   
7659               Tyree Bell           31            Male     Black   
7660      Christopher Tavares           21            Male  Hispanic   
7661        Andrew L. Closson           21            Male     White   
7662            Andrew Layton           26            Male     White   

     Date of Incident (month/day/year)             Street Address of Incident  \
0                             31-12-19                             Broad St.    
1                             31-12-19                         7239-7411 I-40   
2                             31-12-19                         3600 N 24th St   
3                             31-12-19                30800 14th Avenue South   
4                             31-12-19                    17057 N Outer 40 Rd   
...                                ...                                    ...   
7658                          01-01-13                    912 Loma Linda Ave.   
7659                          01-01-13                       3727 N. 42nd St.   
7660                          01-01-13  Highway 50 and North Elizabeth Street   
7661                          01-01-13                        U.S. Highway 53   
7662                          01-01-13                 410 S Riverfront Drive   

              City state  Zipcode      County    County_State  
0            Globe    AZ  85501.0        Gila        Gila, AZ  
1          Memphis    AR  38103.0  Crittenden  Crittenden, AR  
2            Omaha    NE  68110.0     Douglas     Douglas, NE  
3      Federal Way    WA  98003.0        King        King, WA  
4     Chesterfield    MO  63005.0   St. Louis   St. Louis, MO  
...            ...   ...      ...         ...             ...  
7658    Farmington    NM  87401.0    San Juan    San Juan, NM  
7659         Omaha    NE  68111.0     Douglas     Douglas, NE  
7660        Pueblo    CO  81008.0      Pueblo      Pueblo, CO  
7661        Gordon    WI  54838.0     Douglas     Douglas, WI  
7662       Mankato    MN  56001.0  Blue Earth  Blue Earth, MN  

[7663 rows x 11 columns]

In [12]:
kill_df = police_df.groupby(["County_State", "race"]).size()
kill_df = pd.DataFrame(kill_df).reset_index()
total_df = kill_df.pivot_table(columns="race", index='County_State', values=0, fill_value=0)
total_df.reset_index()

race                                       County_State  Asian  Black  \
0                                            Acadia, LA      0      0   
1                                          Acadiana, LA      0      1   
2                                               Ada, ID      0      0   
3                                             Adair, OK      0      0   
4                                             Adams, CO      0      4   
...                                                 ...    ...    ...   
1578                                           York, VA      0      1   
1579                                           Yuba, CA      0      1   
1580                                           Yuma, AZ      0      0   
1581  no county (http://www.ask.com/geography/county...      0      1   
1582                                         orange, CA      0      1   

race  Hispanic  Native American  Pacific Islander  Unknown  White  
0            0                0                 0        1      1  
1            0                0                 0        0      0  
2            3                0                 0        0      9  
3            0                0                 0        0      2  
4            9                1                 0        7     11  
...        ...              ...               ...      ...    ...  
1578         0                0                 0        1      0  
1579         1                0                 0        2      5  
1580         3                0                 0        2      2  
1581         0                0                 0        0      0  
1582         0                0                 0        0      0  

[1583 rows x 8 columns]

In [13]:
census_clean_pd["County_State"] = census_clean_pd.County + ", " + census_clean_pd.State
census_clean_pd

population    white   black  native  asian  native_h   mixed  hispanic  \
0        27690.0  25856.0   318.0   172.0  245.0     143.0   655.0    4021.0   
1        11189.0   4778.0  6070.0    47.0   46.0       0.0    72.0     578.0   
2        22684.0  16387.0  5348.0    39.0  174.0       0.0   400.0    1013.0   
3        15202.0  14632.0    76.0    62.0   26.0       0.0   164.0     275.0   
4        25587.0  24850.0   143.0   103.0  147.0       0.0   279.0     615.0   
...          ...      ...     ...     ...    ...       ...     ...       ...   
3137     44812.0  41314.0   405.0   398.0  276.0     137.0  1532.0    7107.0   
3138     22623.0  20964.0   168.0    95.0  410.0       0.0   226.0    3433.0   
3139     20893.0  19705.0    39.0   204.0   31.0       0.0   634.0    1872.0   
3140      8351.0   7575.0    66.0    47.0   15.0       0.0   327.0    1166.0   
3141      7175.0   6686.0    18.0     9.0  361.0       0.0   101.0      72.0   

     State ID County ID      County State   FIPS    County_State  
0          05       015     Carroll    AR  05015     Carroll, AR  
1          05       017      Chicot    AR  05017      Chicot, AR  
2          05       019       Clark    AR  05019       Clark, AR  
3          05       021        Clay    AR  05021        Clay, AR  
4          05       023    Cleburne    AR  05023    Cleburne, AR  
...       ...       ...         ...   ...    ...             ...  
3137       56       037  Sweetwater    WY  56037  Sweetwater, WY  
3138       56       039       Teton    WY  56039       Teton, WY  
3139       56       041       Uinta    WY  56041       Uinta, WY  
3140       56       043    Washakie    WY  56043    Washakie, WY  
3141       56       045      Weston    WY  56045      Weston, WY  

[3142 rows x 14 columns]

In [18]:
new_tot_df = pd.merge(census_clean_pd, total_df, how='inner', on = ['County_State', 'County_State'])
new_tot_df['p_white'] = new_tot_df.white/new_tot_df.population
df = new_tot_df

In [31]:
df["p_white"] = df.white/df.population
df["p_black"] = df.black/df.population
df["p_native"] = df.native/df.population
df["p_asian"] = df.asian/df.population
df["p_native_h"] = df.native_h/df.population
df["p_mixed"] = df.mixed/df.population
df["p_hispanic"] = df.hispanic/df.population


df = df.rename(columns={"White": "white_dead",
                                      "Black": "black_dead",
                                      "Native American" : "native_dead",
                                      "Asian" : "asian_dead",
                                      "Pacific Islander" : "native_h_dead",
                                      "Hispanic" : "hispanic_dead"})
#total column
df['total'] = df.asian_dead + df.black_dead + df.hispanic_dead + df.native_dead + df.Unknown + df.white_dead


#percentages 
df['perc_white_dead'] = df.white_dead/df.total
df['perc_black_dead'] = df.black_dead/df.total
df['perc_hispanic_dead'] = df.hispanic_dead/df.total
df['perc_native_dead'] = df.native_dead/df.total
df['perc_native_h_dead'] = df.native_h_dead/df.total
df['perc_Unknown_dead'] = df.Unknown/df.total
df['perc_asian_dead'] = df.asian_dead/df.total
df


#measure 1: what percentage of the population is dying by race
df['perc_white_pop'] = (df.white_dead/df.white)*100
df['perc_black_pop'] = (df.black_dead/df.black)*100
df['perc_hispanic_pop'] = (df.hispanic_dead/df.hispanic)*100
df['perc_native_pop'] = (df.native_dead/df.native)*100
df['perc_asian_pop'] = (df.asian_dead/df.asian)*100
df

#measure 2: do the police killings match the demographics?
df['demo_rel_white'] = (df.perc_white_dead/df.p_white)
df['demo_rel_black'] = (df.perc_black_dead/df.p_black)
df['demo_rel_hispanic'] = (df.perc_hispanic_dead/df.p_hispanic)
df['demo_rel_native'] = (df.perc_native_dead/df.p_native)
df['demo_rel_asian'] = (df.perc_asian_dead/df.p_asian)
df


population    white    black  native   asian  native_h   mixed  \
0        15202.0  14632.0     76.0    62.0    26.0       0.0   164.0   
1        24168.0  14506.0   8420.0    76.0   256.0       0.0   245.0   
2        21060.0  17959.0   2490.0   112.0    16.0       0.0   436.0   
3       102884.0  83094.0  14233.0   657.0  1222.0      80.0  1984.0   
4        61927.0  55876.0    825.0  1248.0  1086.0       0.0  1944.0   
...          ...      ...      ...     ...     ...       ...     ...   
1506     14223.0  13532.0     12.0    80.0   123.0       1.0   356.0   
1507     40683.0  29893.0    211.0  8306.0   177.0      30.0  1496.0   
1508     96459.0  85228.0   2760.0   682.0  1120.0     165.0  3256.0   
1509     80871.0  75254.0    964.0   764.0   748.0       6.0  2227.0   
1510     20893.0  19705.0     39.0   204.0    31.0       0.0   634.0   

      hispanic State ID County ID  ... perc_black_pop perc_hispanic_pop  \
0        275.0       05       021  ...       0.000000          0.000000   
1        619.0       05       027  ...       0.011876          0.000000   
2        790.0       05       029  ...       0.000000          0.000000   
3       4856.0       05       031  ...       0.000000          0.000000   
4       4328.0       05       033  ...       0.000000          0.000000   
...        ...      ...       ...  ...            ...               ...   
1506    1094.0       56       009  ...       0.000000          0.091408   
1507    2758.0       56       013  ...       0.000000          0.000000   
1508   13697.0       56       021  ...       0.000000          0.000000   
1509    6630.0       56       025  ...       0.000000          0.000000   
1510    1872.0       56       041  ...       0.000000          0.000000   

     perc_native_pop perc_asian_pop  demo_real_white  demo_rel_white  \
0           0.000000            0.0         1.038956        1.038956   
1           0.000000            0.0         0.000000        0.000000   
2           0.000000            0.0         1.172671        1.172671   
3           0.000000            0.0         0.742898        0.742898   
4           0.000000            0.0         1.108293        1.108293   
...              ...            ...              ...             ...   
1506        0.000000            0.0         0.525532        0.525532   
1507        0.012039            0.0         0.453651        0.453651   
1508        0.146628            0.0         0.565888        0.565888   
1509        0.000000            0.0         1.074641        1.074641   
1510        0.000000            0.0         1.060289        1.060289   

      demo_rel_black  demo_rel_hispanic  demo_rel_native  demo_rel_asian  
0           0.000000           0.000000         0.000000             0.0  
1           2.870309           0.000000         0.000000             0.0  
2           0.000000           0.000000         0.000000             0.0  
3           0.000000           0.000000         0.000000             0.0  
4           0.000000           0.000000         0.000000             0.0  
...              ...                ...              ...             ...  
1506        0.000000           6.500457         0.000000             0.0  
1507        0.000000           0.000000         1.632675             0.0  
1508        0.000000           0.000000        70.717742             0.0  
1509        0.000000           0.000000         0.000000             0.0  
1510        0.000000           0.000000         0.000000             0.0  

[1511 rows x 47 columns]

In [87]:
df.columns

Index(['population', 'white', 'black', 'native', 'asian', 'native_h', 'mixed',
       'hispanic', 'State ID', 'County ID', 'County', 'State', 'FIPS',
       'County_State', 'asian_dead', 'black_dead', 'hispanic_dead',
       'native_dead', 'native_h_dead', 'Unknown', 'white_dead', 'p_white',
       'p_black', 'p_native', 'p_asian', 'p_native_h', 'p_mixed', 'p_hispanic',
       'total', 'perc_white_dead', 'perc_black_dead', 'perc_hispanic_dead',
       'perc_native_dead', 'perc_native_h_dead', 'perc_Unknown_dead',
       'perc_asian_dead', 'perc_white_pop', 'perc_black_pop',
       'perc_hispanic_pop', 'perc_native_pop', 'perc_asian_pop',
       'demo_real_white', 'demo_rel_white', 'demo_rel_black',
       'demo_rel_hispanic', 'demo_rel_native', 'demo_rel_asian'],
      dtype='object')

In [100]:
fips = df.FIPS

#[df['State ID'] =="29"]

values = df.demo_rel_hispanic
#[df['State ID'] =="29"]

colorscale = ["#f7fbff","#ebf3fb","#deebf7","#d2e3f3","#c6dbef","#b3d2e9","#9ecae1",
              "#85bcdb","#6baed6","#57a0ce","#4292c6","#3082be","#2171b5","#1361a9",
              "#08519c","#0b4083","#08306b"]
endpts = list(np.linspace(1, 10, len(colorscale) - 1))

fig = ff.create_choropleth(fips=fips, 
                           values=values, 
                           state_outline={'width': 1}, 
                           binning_endpoints=endpts, 
                           colorscale=colorscale,
                           legend_title='Factors Greater',
                           title='Black Death % vs. Area Demographics')
fig.layout.template = None
fig['layout']['xaxis']['fixedrange'] = False 
fig['layout']['yaxis']['fixedrange'] = False 
fig.show()

In [59]:
fips = df.FIPS[df['State ID'] =="29"]

values = df.perc_black_pop[df['State ID'] =="29"]

fig = ff.create_choropleth(fips=fips, values=values,state_outline={'width': 1}, county_outline={'color': 'rgb(15, 15, 55)', 'width': 0.5})
fig.layout.template = None
fig['layout']['xaxis']['fixedrange'] = False 
fig['layout']['yaxis']['fixedrange'] = False 
fig.show()

In [54]:
fips = df.FIPS[df['State ID'] =="29"]

values = df.demo_rel_black[df['State ID'] =="29"]

fig = ff.create_choropleth(fips=fips, values=values,state_outline={'width': 1}, county_outline={'color': 'rgb(15, 15, 55)', 'width': 0.5})
fig.layout.template = None
fig['layout']['xaxis']['fixedrange'] = False 
fig['layout']['yaxis']['fixedrange'] = False 
fig.show()

In [53]:
fips = df.FIPS[df['State ID'] =="49"]

values = df.demo_rel_black[df['State ID'] =="49"]

fig = ff.create_choropleth(fips=fips, values=values,state_outline={'width': 1}, county_outline={'color': 'rgb(15, 15, 55)', 'width': 0.5})
fig.layout.template = None
fig['layout']['xaxis']['fixedrange'] = False 
fig['layout']['yaxis']['fixedrange'] = False 
fig.show()

In [73]:
df.columns

Index(['population', 'white', 'black', 'native', 'asian', 'native_h', 'mixed',
       'hispanic', 'State ID', 'County ID', 'County', 'State', 'FIPS',
       'County_State', 'asian_dead', 'black_dead', 'hispanic_dead',
       'native_dead', 'native_h_dead', 'Unknown', 'white_dead', 'p_white',
       'p_black', 'p_native', 'p_asian', 'p_native_h', 'p_mixed', 'p_hispanic',
       'total', 'perc_white_dead', 'perc_black_dead', 'perc_hispanic_dead',
       'perc_native_dead', 'perc_native_h_dead', 'perc_Unknown_dead',
       'perc_asian_dead', 'perc_white_pop', 'perc_black_pop',
       'perc_hispanic_pop', 'perc_native_pop', 'perc_asian_pop',
       'demo_real_white', 'demo_rel_white', 'demo_rel_black',
       'demo_rel_hispanic', 'demo_rel_native', 'demo_rel_asian'],
      dtype='object')

In [102]:
fig = px.scatter(df, x="p_black", y="demo_rel_black", color = "black_dead", trendline = 'ols', 
                 title="Correlation between death disproportionality and population demographics (FIPS, Black)", log_y=True)

fig.show()
